In [1]:
import pandas as pd
import requests
import pickle
import math
import folium
import numpy as np
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.metrics.pairwise import haversine_distances
from math import radians, sin, cos, sqrt, atan2

In [1]:
bus = pd.read_csv('Bus_Stops.csv')a
bus

Street_One         Street_Two
0    MISSION ST          ITALY AVE
1    MISSION ST  NEW MONTGOMERY ST
2    MISSION ST            01ST ST
3    MISSION ST            20TH ST
4    MISSION ST         FREMONT ST
..          ...                ...
114  MISSION ST        NIAGARA AVE
115  MISSION ST           ACTON ST
116  MISSION ST            05TH ST
117  MISSION ST            24TH ST
118  MISSION ST           GRACE ST

[119 rows x 2 columns]

In [2]:
emp = pd.read_csv('Employee_Addresses.csv')
emp

address  employee_id
0      98 Edinburgh St, San Francisco, CA 94112, USA          206
1           237 Accacia St, Daly City, CA 94014, USA         2081
2       1835 Folsom St, San Francisco, CA 94103, USA          178
3     170 Cambridge St, San Francisco, CA 94134, USA           50
4        16 Roanoke St, San Francisco, CA 94131, USA         1863
...                                              ...          ...
2186     72 Topeka Ave, San Francisco, CA 94124, USA          980
2187         330 Oliver St, Daly City, CA 94014, USA          385
2188     94 W View Ave, San Francisco, CA 94134, USA          692
2189   1599 Geneva Ave, San Francisco, CA 94112, USA         1025
2190     499 Treat Ave, San Francisco, CA 94110, USA         1782

[2191 rows x 2 columns]

## Automating API calls in functions for 2 different APIs to test each one's accuracy

In [2]:
def here_api_getloc(address):
    req = f'https://geocode.search.hereapi.com/v1/geocode?q={address}&apiKey=WbwO5-aji8yjbH9nk-voiww72dty2a2iPcwFFRMwYRQ'
    resp = requests.get(req)
    long =  resp.json()['items'][0]['position']['lng']
    lat = resp.json()['items'][0]['position']['lat']
    return (lat, long)

def geoapify_api_getloc(address):
    req = f'https://api.geoapify.com/v1/geocode/search?text={address}&apiKey=d5aca9a4b86c4063b9f41dd617bc2704'
    resp = requests.get(req)
    return tuple(resp.json()['features'][0]['geometry']['coordinates'])[::-1]

## Geocode the bus stops locations

In [90]:
bus['location'] = bus['Street_One']+', '+bus['Street_Two'] + ', CA, USA'
bus

Street_One         Street_Two                                location
0    MISSION ST          ITALY AVE          MISSION ST, ITALY AVE, CA, USA
1    MISSION ST  NEW MONTGOMERY ST  MISSION ST, NEW MONTGOMERY ST, CA, USA
2    MISSION ST            01ST ST            MISSION ST, 01ST ST, CA, USA
3    MISSION ST            20TH ST            MISSION ST, 20TH ST, CA, USA
4    MISSION ST         FREMONT ST         MISSION ST, FREMONT ST, CA, USA
..          ...                ...                                     ...
114  MISSION ST        NIAGARA AVE        MISSION ST, NIAGARA AVE, CA, USA
115  MISSION ST           ACTON ST           MISSION ST, ACTON ST, CA, USA
116  MISSION ST            05TH ST            MISSION ST, 05TH ST, CA, USA
117  MISSION ST            24TH ST            MISSION ST, 24TH ST, CA, USA
118  MISSION ST           GRACE ST           MISSION ST, GRACE ST, CA, USA

[119 rows x 3 columns]

In [91]:
bus['lat & long'] = bus['location'].apply(here_api_getloc)
bus

Street_One         Street_Two                                location  \
0    MISSION ST          ITALY AVE          MISSION ST, ITALY AVE, CA, USA   
1    MISSION ST  NEW MONTGOMERY ST  MISSION ST, NEW MONTGOMERY ST, CA, USA   
2    MISSION ST            01ST ST            MISSION ST, 01ST ST, CA, USA   
3    MISSION ST            20TH ST            MISSION ST, 20TH ST, CA, USA   
4    MISSION ST         FREMONT ST         MISSION ST, FREMONT ST, CA, USA   
..          ...                ...                                     ...   
114  MISSION ST        NIAGARA AVE        MISSION ST, NIAGARA AVE, CA, USA   
115  MISSION ST           ACTON ST           MISSION ST, ACTON ST, CA, USA   
116  MISSION ST            05TH ST            MISSION ST, 05TH ST, CA, USA   
117  MISSION ST            24TH ST            MISSION ST, 24TH ST, CA, USA   
118  MISSION ST           GRACE ST           MISSION ST, GRACE ST, CA, USA   

                 lat & long  
0    (37.71847, -122.43953)  
1     (37.78745, -122.4005)  
2     (37.7788, -122.41144)  
3    (35.76182, -120.69529)  
4    (37.79047, -122.39669)  
..                      ...  
114  (37.71558, -122.44172)  
115   (37.7088, -122.45276)  
116   (37.7788, -122.41144)  
117  (37.75226, -122.41849)  
118  (37.77561, -122.41549)  

[119 rows x 4 columns]

In [118]:
# to remove outliers in data which is detected when plotting on the map
bus = bus[bus['lat & long'].apply(lambda x: (math.trunc(x[0]) == 37) & (math.trunc(x[1]) < -120 ) )]

In [131]:
bus = bus.reset_index()
bus = bus.rename(columns={"index":"ID"})
bus

ID  Street_One         Street_Two  \
0      0  MISSION ST          ITALY AVE   
1      1  MISSION ST  NEW MONTGOMERY ST   
2      2  MISSION ST            01ST ST   
3      3  MISSION ST         FREMONT ST   
4      4  MISSION ST            ERIE ST   
..   ...         ...                ...   
107  107  MISSION ST        NIAGARA AVE   
108  108  MISSION ST           ACTON ST   
109  109  MISSION ST            05TH ST   
110  110  MISSION ST            24TH ST   
111  111  MISSION ST           GRACE ST   

                                   location              lat & long  
0            MISSION ST, ITALY AVE, CA, USA  (37.71847, -122.43953)  
1    MISSION ST, NEW MONTGOMERY ST, CA, USA   (37.78745, -122.4005)  
2              MISSION ST, 01ST ST, CA, USA   (37.7788, -122.41144)  
3           MISSION ST, FREMONT ST, CA, USA  (37.79047, -122.39669)  
4              MISSION ST, ERIE ST, CA, USA  (37.76907, -122.42004)  
..                                      ...                     ...  
107        MISSION ST, NIAGARA AVE, CA, USA  (37.71558, -122.44172)  
108           MISSION ST, ACTON ST, CA, USA   (37.7088, -122.45276)  
109            MISSION ST, 05TH ST, CA, USA   (37.7788, -122.41144)  
110            MISSION ST, 24TH ST, CA, USA  (37.75226, -122.41849)  
111           MISSION ST, GRACE ST, CA, USA  (37.77561, -122.41549)  

[112 rows x 5 columns]

In [2]:

# Saved as pickle not csv to avoid converting the tuple to string
# with open('bus_stops_final.pkl', 'wb') as f:
#     pickle.dump(bus, f)

with open('bus_stops_final.pkl', 'rb') as f:
    bus_stops = pickle.load(f)
    
bus_stops

ID  Street_One         Street_Two  \
0      0  MISSION ST          ITALY AVE   
1      1  MISSION ST  NEW MONTGOMERY ST   
2      2  MISSION ST            01ST ST   
3      3  MISSION ST         FREMONT ST   
4      4  MISSION ST            ERIE ST   
..   ...         ...                ...   
107  107  MISSION ST        NIAGARA AVE   
108  108  MISSION ST           ACTON ST   
109  109  MISSION ST            05TH ST   
110  110  MISSION ST            24TH ST   
111  111  MISSION ST           GRACE ST   

                                   location              lat & long  
0            MISSION ST, ITALY AVE, CA, USA  (37.71847, -122.43953)  
1    MISSION ST, NEW MONTGOMERY ST, CA, USA   (37.78745, -122.4005)  
2              MISSION ST, 01ST ST, CA, USA   (37.7788, -122.41144)  
3           MISSION ST, FREMONT ST, CA, USA  (37.79047, -122.39669)  
4              MISSION ST, ERIE ST, CA, USA  (37.76907, -122.42004)  
..                                      ...                     ...  
107        MISSION ST, NIAGARA AVE, CA, USA  (37.71558, -122.44172)  
108           MISSION ST, ACTON ST, CA, USA   (37.7088, -122.45276)  
109            MISSION ST, 05TH ST, CA, USA   (37.7788, -122.41144)  
110            MISSION ST, 24TH ST, CA, USA  (37.75226, -122.41849)  
111           MISSION ST, GRACE ST, CA, USA  (37.77561, -122.41549)  

[112 rows x 5 columns]

## The Code used to geocode the employees addresses on several days
(HERE API has limited number of requests per day)

In [3]:
with open('employees_final.pkl', 'rb') as f:
    employees = pickle.load(f)
employees

address  employee_id  \
0      98 Edinburgh St, San Francisco, CA 94112, USA          206   
1           237 Accacia St, Daly City, CA 94014, USA         2081   
2       1835 Folsom St, San Francisco, CA 94103, USA          178   
3     170 Cambridge St, San Francisco, CA 94134, USA           50   
4        16 Roanoke St, San Francisco, CA 94131, USA         1863   
...                                              ...          ...   
2186     72 Topeka Ave, San Francisco, CA 94124, USA          980   
2187         330 Oliver St, Daly City, CA 94014, USA          385   
2188     94 W View Ave, San Francisco, CA 94134, USA          692   
2189   1599 Geneva Ave, San Francisco, CA 94112, USA         1025   
2190     499 Treat Ave, San Francisco, CA 94110, USA         1782   

                  lat & long  
0     (37.72763, -122.42734)  
1     (37.70418, -122.41582)  
2      (37.76793, -122.4151)  
3     (37.72966, -122.41972)  
4     (37.73624, -122.43132)  
...                      ...  
2186   (37.7341, -122.40006)  
2187  (37.70531, -122.44851)  
2188  (37.73079, -122.41717)  
2189   (37.71244, -122.4296)  
2190  (37.76231, -122.41379)  

[2188 rows x 3 columns]

In [6]:
first_index = 1891 # is the first index of the null values that need to be generated
steps = 299        # the number of addresses that need to be geocoded
employees.loc[first_index:first_index+steps,'lat & long'] = employees.loc[first_index:first_index+steps,'address'].apply(here_api_getloc)
employees

address  employee_id  \
0      98 Edinburgh St, San Francisco, CA 94112, USA          206   
1           237 Accacia St, Daly City, CA 94014, USA         2081   
2       1835 Folsom St, San Francisco, CA 94103, USA          178   
3     170 Cambridge St, San Francisco, CA 94134, USA           50   
4        16 Roanoke St, San Francisco, CA 94131, USA         1863   
...                                              ...          ...   
2186     72 Topeka Ave, San Francisco, CA 94124, USA          980   
2187         330 Oliver St, Daly City, CA 94014, USA          385   
2188     94 W View Ave, San Francisco, CA 94134, USA          692   
2189   1599 Geneva Ave, San Francisco, CA 94112, USA         1025   
2190     499 Treat Ave, San Francisco, CA 94110, USA         1782   

                  lat & long  
0     (37.72763, -122.42734)  
1     (37.70418, -122.41582)  
2      (37.76793, -122.4151)  
3     (37.72966, -122.41972)  
4     (37.73624, -122.43132)  
...                      ...  
2186   (37.7341, -122.40006)  
2187  (37.70531, -122.44851)  
2188  (37.73079, -122.41717)  
2189   (37.71244, -122.4296)  
2190  (37.76231, -122.41379)  

[2191 rows x 3 columns]

In [7]:
employees[employees['lat & long'].isna()]

Empty DataFrame
Columns: [address, employee_id, lat & long]
Index: []

In [8]:
# with open('employees_final.pkl', 'wb') as f:
#     pickle.dump(employees, f)


I found a misgeocoded address (out of San Francisco), for simplicity I'll simply remove it

In [61]:
# employees = employees[employees['lat & long'].apply(lambda x: (math.trunc(x[0]) < 38) and(math.trunc(x[0]) > 35   )   )]
# with open('employees_final.pkl', 'wb') as f:
#     pickle.dump(employees, f)


## Extracting the geocoding of both locations and prepare them for plotting

In [4]:
emp_locs = employees[employees['lat & long'].notna()]['lat & long'].values.tolist()
bus_stops_locs = bus_stops['lat & long'].values.tolist()

A Function to plot the bus stops locations and employees locations on the map

In [5]:
def plot_locs(bus_locs, emp_locs):
    location_sets = {
        'Bus stops': bus_locs,
        'Employess': emp_locs
    }

    # Create a map centered around the first coordinate
    location = []
    if len(bus_locs) == 0:
        location = list(location_sets.values())[1][0]
    else:
        location = list(location_sets.values())[0][0]
    map = folium.Map(location=location, zoom_start=4)

    # Define a color palette for each set
    color_palette = ['#FF0000', '#0000FF', '#0000FF']

    # Add markers for each set of locations with different colors
    for i, (set_name, locations) in enumerate(location_sets.items()):
        color = color_palette[i % len(color_palette)]  # Cycles through the color palette
        for coord in locations:
            folium.CircleMarker(location=coord, color=color, radius=7, fill = True).add_to(map)

    # Display the map
    return map


In [6]:
plot_locs( bus_stops_locs ,emp_locs)

## Start solving the problem of finding the most optimum 10 bus stops that minimizes the average walking distance between the employees and their assigned bus stop

It turns out that using Haversine distance in our calculations yields more accurate results

I can use APIs to get precise walking distance bewteen employees and bus stops. But decreasing the Haversine distance will by average decrease that walking distance anyways

## I'll try multiple clustering methods and see the output to decide how to solve the problem
- Cluster employees using KMeans
- Cluster Bus stops into 10 clusters and use the centroids to assign employees to them
- Cluster employees using KMeans such that:
    1) Cluster centroids must be replaced with the nearest bus stop
    2) Reasign employees to the neareest bus stop (from the chosen 10)
    3) Update the chosen bus stops by recalculating the cluster centroids and repeat the process again
    
    

###  Cluster employees using KMeans

In [7]:
def kmeans_clustering(points, k):
    # Convert points to numpy array
    points_array = np.array(points)
    
    kmeans = KMeans(n_clusters=k)
    kmeans.fit(points_array)
    labels = kmeans.labels_

    points_with_labels = []
    for i, point in enumerate(points):
        label = labels[i]
        points_with_labels.append((*point, label))

    return points_with_labels


In [8]:
clustered = kmeans_clustering(employees['lat & long'].values.tolist(), 10)

C:\Users\marwa\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


A function that will be used to plot any clustered points with different colors

In [9]:
def plot_locs2(bus_locs, clustered_emp):
    
    # Create a map centered around the first employee location
    location = clustered_emp[0][:2]
    map = folium.Map(location=location, zoom_start=4)

    # Define a color palette for clusters    
    color_palette = ['#FF0000', '#00FF00', '#0000FF', '#FF00FF', '#00FFFF', '#FFFF00', '#800080', '#228B22',
                 '#FF1493', '#4169E1']
                     

    
    # Add markers for employee locations with different colors based on cluster label
    for lat,long,label in clustered_emp:
        loc = (lat,long)
        label = int(label)
        color = color_palette[int(label) % len(color_palette)]  # Cycles through the color palette
        folium.CircleMarker(location=loc, color=color, radius=7, fill=True).add_to(map)

    # Add markers for bus locations (without clustering) in a separate color
    for loc in bus_locs:
        color = '#000000'  # Black color for bus locations
        folium.CircleMarker(location=loc, color=color, radius=7, fill=True).add_to(map)

    # Display the map
    return map


In [10]:
plot_locs2(bus_stops_locs, clustered )

Using these cluster centroids to choose the nearest bus stop for each will not be a good solution 

Since the employees clusters are not in a proper distribution with respect to the bus stops locations

###  Cluster Bus stops into 10 clusters and use the centroids to assign employees to them

A function that calculates the Haversine distance for us in kilometers

In [11]:
def haversine_distance(list1, list2):
    
    distances = []
    
    for point1 in list1:
        for point2 in list2:
            # Extract latitude and longitude coordinates from the tuples
            lat1, lon1 = point1
            lat2, lon2 = point2

            # Convert latitude and longitude to radians
            lat1_rad = radians(lat1)
            lon1_rad = radians(lon1)
            lat2_rad = radians(lat2)
            lon2_rad = radians(lon2)

            # Haversine formula
            dlon = lon2_rad - lon1_rad
            dlat = lat2_rad - lat1_rad
            a = sin(dlat/2)**2 + cos(lat1_rad) * cos(lat2_rad) * sin(dlon/2)**2
            c = 2 * atan2(sqrt(a), sqrt(1-a))
            distance = 6371 * c  # Earth radius in kilometers
            distances.append(distance)

    return distances


This function will cluster the bus stops into 10 clusters and assign each employee to the nearest centroid

In [12]:
def assign_points(bus_stops, employees):
    
    bus_stops = np.array(bus_stops)
    employees = np.array(employees)

    # Initialize KMeans with 10 clusters
    kmeans = KMeans(n_clusters=10)

    # Fit KMeans on the array of 119 points
    kmeans.fit(bus_stops)

    # Get the cluster labels assigned by KMeans
    cluster_labels = kmeans.labels_

    # Make sure that the centroid is an actual bus stop location and not a midpoint
    centroids = kmeans.cluster_centers_
    for i in range(len(centroids)):
        distances = haversine_distance([centroids[i]], bus_stops)
        centroids[i] = bus_stops[np.argmin(distances)]

    # Assign each employee to the nearest bus stop
    assigned_points = []
    for point in employees:
        distances = haversine_distance([point], centroids)
        closest_centroid_idx = np.argmin(distances)
        assigned_points.append((*point, closest_centroid_idx))

    return assigned_points, centroids


In [15]:
clustered,bus_stops_locations = assign_points(bus_stops_locs, emp_locs)

C:\Users\marwa\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


Plotting the clustered employees and the chosen bus stops only

In [16]:
plot_locs2(bus_stops_locations, clustered)

The previous clustering method allows a better clusters shapes but the chosen bus stops are not optimum at all

### Cluster employees using KMeans and update the chosen bus stops
    With the method mentioned earlier:
        1) Cluster centroids must be replaced with the nearest bus stop
        2) Reasign employees to the neareest bus stop (from the chosen 10)
        3) Update the chosen bus stops by recalculating the cluster centroids and repeat the process again

In [20]:
def assign_points2(bus_stops, employees, updates):
    
    unclustered_employees = employees.copy()
    employees = employees[employees['lat & long'].notna()]['lat & long'].values.tolist()
    bus_stops = bus_stops['lat & long'].values.tolist()
    # Convert arrays to numpy arrays
    bus_stops = np.array(bus_stops)
    employees = np.array(employees)

    # Initialize KMeans with 10 clusters
    kmeans = KMeans(n_clusters=10, random_state = 7)

    # Fit KMeans on the array of 119 points
    kmeans.fit(employees)

    # Get the cluster labels assigned by KMeans
    cluster_labels = kmeans.labels_

    # Calculate the centroids of each cluster
    centroids = kmeans.cluster_centers_
    assigned_points = []
    emp_clustered = {0:[],1:[],2:[],3:[],4:[],5:[],6:[],7:[],8:[],9:[]}
    chosen10 = []
    
    for j in range(updates):
        
        if j != 0:
            for key in emp_clustered:
                emps = len(emp_clustered[key])
                centroids[key] = tuple(sum(col) / emps for col in zip(*emp_clustered[key]))
        
        chosen10 = []
        for i in range(len(centroids)):
            distances = haversine_distance([centroids[i]], bus_stops)
            centroids[i] = bus_stops[np.argmin(distances)]
            chosen10.append([i, tuple(centroids[i])])        
        # Assign each point in the array of n points to the centroid with the minimum distance
            
        for key in emp_clustered:
                emp_clustered[key] = []
                
        assigned_points = []
        
        for point in employees:
            distances = haversine_distance([point], centroids)
            closest_centroid_idx = np.argmin(distances)
            emp_clustered[closest_centroid_idx].append(tuple(point))
            assigned_points.append((*point, closest_centroid_idx))
            
        
    chosen10 = pd.DataFrame(chosen10).rename(columns={0: 'id',1:'location'})
    clustered_employees = unclustered_employees
    clustered_employees['bus_stop']= [ i[2] for i in assigned_points]
    
    return assigned_points, clustered_employees, chosen10


First use the updating parameter equal to 1 to update the chosen bus stops once

In [21]:
solution,emps,chosen10 = assign_points2(bus_stops, employees, 1)

C:\Users\marwa\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [22]:
plot_locs2(chosen10['location'].values.tolist(), solution)

Seems better than the previous solution.

Since employees clusters and their chosen bus stop are getting closer to each other

Lets use a larger updating paramter 

In [23]:
solution,clustered_employees,chosen10 = assign_points2(bus_stops, employees, 6)

C:\Users\marwa\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [24]:
plot_locs2(chosen10['location'].values.tolist(), solution)

As you can see, it looks pretty good, its the best solution so far

Lets associate the chosen bus stop for each employee with the actual bus stop ID

In [27]:
def associate(stops, chosen, emp):
    final = pd.merge(emp,chosen, left_on = 'bus_stop', right_on = 'id')
    final.drop(['id'], axis = 1, inplace = True)
    final = pd.merge(final, stops, left_on = 'location', right_on = 'lat & long')
    final = final[['address','employee_id', 'lat & long_x', 'ID']]
    final.rename(columns = {'lat & long_x': 'lat & long', 'ID': 'bus_stop_id'}, inplace = True)
    display(final)
    return final
    
employees_assigned = associate(bus_stops,chosen10, clustered_employees)

address  employee_id  \
0     98 Edinburgh St, San Francisco, CA 94112, USA          206   
1        43 Ervine St, San Francisco, CA 94134, USA          933   
2      669 Silver Ave, San Francisco, CA 94134, USA         1905   
3      1608 Felton St, San Francisco, CA 94134, USA          997   
4      330 Harvard St, San Francisco, CA 94134, USA         1797   
...                                             ...          ...   
2183          Plum St, San Francisco, CA 94103, USA         1712   
2184     1617 13th St, San Francisco, CA 94103, USA         2060   
2185   1844 Market St, San Francisco, CA 94102, USA          833   
2186       70 13th St, San Francisco, CA 94103, USA           28   
2187     1676 13th St, San Francisco, CA 94103, USA          947   

                  lat & long  bus_stop_id  
0     (37.72763, -122.42734)           14  
1     (37.71694, -122.40854)           14  
2       (37.729, -122.42217)           14  
3     (37.72597, -122.42099)           14  
4     (37.72535, -122.42047)           14  
...                      ...          ...  
2183  (37.77093, -122.41879)           38  
2184  (37.76974, -122.41667)           38  
2185  (37.77143, -122.42437)           38  
2186  (37.76981, -122.41495)           38  
2187  (37.76974, -122.41667)           38  

[2188 rows x 4 columns]

## Reporting

Find the average distance between employees and their assigned bus stops

In [29]:
def get_distance(emp, bus):
    df = pd.merge(emp,bus, left_on = 'bus_stop_id', right_on = 'ID')
    df['distance'] = df.apply(lambda row: haversine_distance([row['lat & long_x']], [row['lat & long_y']])[0], axis=1)
    return round(df['distance'].mean(),2)
str(get_distance(employees_assigned,bus_stops))+' KM'

'1.09 KM'

## Save files

Save employees csv

In [31]:
employees_assigned.drop(['lat & long'], axis = 1, inplace = True)
employees_assigned

address  employee_id  bus_stop_id
0     98 Edinburgh St, San Francisco, CA 94112, USA          206           14
1        43 Ervine St, San Francisco, CA 94134, USA          933           14
2      669 Silver Ave, San Francisco, CA 94134, USA         1905           14
3      1608 Felton St, San Francisco, CA 94134, USA          997           14
4      330 Harvard St, San Francisco, CA 94134, USA         1797           14
...                                             ...          ...          ...
2183          Plum St, San Francisco, CA 94103, USA         1712           38
2184     1617 13th St, San Francisco, CA 94103, USA         2060           38
2185   1844 Market St, San Francisco, CA 94102, USA          833           38
2186       70 13th St, San Francisco, CA 94103, USA           28           38
2187     1676 13th St, San Francisco, CA 94103, USA          947           38

[2188 rows x 3 columns]

In [33]:
# employees_assigned.to_csv('employee_assigned.csv')

Save chosen bus stops csv

In [51]:
chosen_bus_stops = pd.merge(chosen10,bus_stops, left_on = 'location', right_on = 'lat & long')
chosen_bus_stops = chosen_bus_stops[['ID', 'Street_One','Street_Two', 'location_y']].rename(columns = {'location_y':'location'})

In [52]:
chosen_bus_stops

ID  Street_One     Street_Two                            location
0  34  MISSION ST   VIRGINIA AVE   MISSION ST, VIRGINIA AVE, CA, USA
1  60  MISSION ST        14TH ST        MISSION ST, 14TH ST, CA, USA
2  64  MISSION ST   LAWRENCE AVE   MISSION ST, LAWRENCE AVE, CA, USA
3  14  MISSION ST    TRUMBULL ST    MISSION ST, TRUMBULL ST, CA, USA
4  70  MISSION ST   LAFAYETTE ST   MISSION ST, LAFAYETTE ST, CA, USA
5  74  MISSION ST  HARRINGTON ST  MISSION ST, HARRINGTON ST, CA, USA
6  38  MISSION ST        PLUM ST        MISSION ST, PLUM ST, CA, USA
7  25  MISSION ST     GENEVA AVE     MISSION ST, GENEVA AVE, CA, USA
8   9  MISSION ST     ANTHONY ST     MISSION ST, ANTHONY ST, CA, USA
9  57  MISSION ST   RICHLAND AVE   MISSION ST, RICHLAND AVE, CA, USA

In [53]:
# chosen_bus_stops.to_csv('chosen_bus_stops.csv')